In [56]:
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.chrome.options import Options
import pandas as pd
import time
import soccerdata as sd

# Find Schedule

In [70]:
# Create a scraper class instance for the 2020/21 Premier League
year = ['1718','1819','2122','2223','2324','2425']
for season in year:
    fbref = sd.FBref('ENG-Premier League', season)
    
    # Fetch data
    games = fbref.read_schedule()
    options = Options()
    options.add_argument('--headless=new')

    # Make Chrome look more like a real browser
    options.add_argument('--disable-blink-features=AutomationControlled')
    options.add_experimental_option("excludeSwitches", ["enable-automation"])
    options.add_experimental_option('useAutomationExtension', False)
    options.add_argument('user-agent=Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/120.0.0.0 Safari/537.36')
    root_url = 'https://fbref.com'
    games['match_report'] = root_url + games['match_report']
    for url in games['match_report']:
        driver = webdriver.Chrome(options = options)
        try:
            driver.get(url)
            time.sleep(3)
            
            # Get page title to identify teams
            page_title = driver.title
            # Usually: "Southampton vs Arsenal Match Summary | May 25, 2025"
            
            if 'vs.' in page_title:
                home_team = page_title.split('vs.')[0].strip()
                away_team = page_title.split('vs.')[1].split('Match')[0].strip()
                date = ' '.join(page_title.split()[-5:-2])
            else:
                home_team = "can't find vs1"
                away_team = "can't find vs2"
            
            print(f"Home: {home_team}")
            print(f"Away: {away_team}")
            print(f"Time: {time}")
            # Find all summary tables
            tables = driver.find_elements(By.CSS_SELECTOR, "table[id*='stats_'][id*='summary']")
            
            # Process home team table (first summary table without '_a')
            home_tables = [t for t in tables if '_a' not in t.get_attribute('id')]
            if home_tables:
                home_html = home_tables[0].get_attribute('outerHTML')
                df_home = pd.read_html(home_html)[0]
                
                # Add Team column
                df_home['Team'] = home_team
                
                # print(f"\n{home_team} Players with Team Column:")
                # print(df_home[[('Unnamed: 0_level_0', 'Player'), ('Team', '')]].head())
                df_home.to_csv(f'{home_team}_players_with_team_{date}.csv', index=False)
            
            # Process away team table (summary table with '_a')
            # away_tables = [t for t in tables if '_a' in t.get_attribute('id')]
            away_tables = home_tables
            if away_tables:
                away_html = away_tables[-1].get_attribute('outerHTML')
                df_away = pd.read_html(away_html)[0]
                
                # Add Team column
                df_away['Team'] = away_team
                
                # print(f"\n{away_team} Players with Team Column:")
                # print(df_away[[('Unnamed: 0_level_0', 'Player'), ('Team', '')]].head())
                df_away.to_csv(f'{away_team}_players_with_team_{date}.csv', index=False)
            
            # Combine both teams
            if home_tables and away_tables:
                combined_df = pd.concat([df_home, df_away], ignore_index=True)
                # print(f"\nCombined DataFrame ({len(combined_df)} players):")
                # print(combined_df[[('Unnamed: 0_level_0', 'Player'), ('Team', '')]].head(10))
                combined_df.to_csv(f'{home_team}_{away_team}_{date}.csv', index=False)
        
        finally:
            driver.quit()

[12/16/25 00:43:59] INFO     Saving cached data to C:\Users\ASUS\soccerdata\data\FBref               ]8;id=874334;file://C:\Users\ASUS\anaconda3\envs\fb\lib\site-packages\soccerdata\_common.py\_common.py]8;;\:]8;id=440631;file://C:\Users\ASUS\anaconda3\envs\fb\lib\site-packages\soccerdata\_common.py#263\263]8;;\

                    WARNING  C:\Users\ASUS\anaconda3\envs\fb\lib\site-packages\soccerdata\fbref.py: ]8;id=320288;file://C:\Users\ASUS\anaconda3\envs\fb\lib\warnings.py\warnings.py]8;;\:]8;id=383450;file://C:\Users\ASUS\anaconda3\envs\fb\lib\warnings.py#109\109]8;;\
                             165: FutureWarning: The behavior of DataFrame concatenation with empty                
                             or all-NA entries is deprecated. In a future version, this will no                    
                             longer exclude empty or all-NA columns when determining the result                    
                             dtypes. To retain the old behavior, exclude the relevant entries                      
                             before the concat operation.                                                          
                               pd.concat(dfs)                                                                      
                                                                                                                   

Home: Arsenal
Away: Leicester City
Time: <module 'time' (built-in)>


[12/16/25 00:44:07] WARNING  C:\Users\ASUS\AppData\Local\Temp\ipykernel_27668\1651500141.py:46:     ]8;id=875905;file://C:\Users\ASUS\anaconda3\envs\fb\lib\warnings.py\warnings.py]8;;\:]8;id=615045;file://C:\Users\ASUS\anaconda3\envs\fb\lib\warnings.py#109\109]8;;\
                             FutureWarning: Passing literal html to 'read_html' is deprecated and                  
                             will be removed in a future version. To read from a literal string,                   
                             wrap it in a 'StringIO' object.                                                       
                               df_home = pd.read_html(home_html)[0]                                                
                                                                                                                   

                    WARNING  C:\Users\ASUS\AppData\Local\Temp\ipykernel_27668\1651500141.py:60:     ]8;id=322715;file://C:\Users\ASUS\anaconda3\envs\fb\lib\warnings.py\warnings.py]8;;\:]8;id=325025;file://C:\Users\ASUS\anaconda3\envs\fb\lib\warnings.py#109\109]8;;\
                             FutureWarning: Passing literal html to 'read_html' is deprecated and                  
                             will be removed in a future version. To read from a literal string,                   
                             wrap it in a 'StringIO' object.                                                       
                               df_away = pd.read_html(away_html)[0]                                                
                                                                                                                   

...

                    WARNING  C:\Users\ASUS\AppData\Local\Temp\ipykernel_27668\1651500141.py:60:     ]8;id=10819;file://C:\Users\ASUS\anaconda3\envs\fb\lib\warnings.py\warnings.py]8;;\:]8;id=514149;file://C:\Users\ASUS\anaconda3\envs\fb\lib\warnings.py#109\109]8;;\
                             FutureWarning: Passing literal html to 'read_html' is deprecated and                  
                             will be removed in a future version. To read from a literal string,                   
                             wrap it in a 'StringIO' object.                                                       
                               df_away = pd.read_html(away_html)[0]                                                
                                                                                                                   

Home: Southampton
Away: Newcastle United
Time: <module 'time' (built-in)>


[12/16/25 03:46:21] WARNING  C:\Users\ASUS\AppData\Local\Temp\ipykernel_27668\1651500141.py:46:     ]8;id=697533;file://C:\Users\ASUS\anaconda3\envs\fb\lib\warnings.py\warnings.py]8;;\:]8;id=692958;file://C:\Users\ASUS\anaconda3\envs\fb\lib\warnings.py#109\109]8;;\
                             FutureWarning: Passing literal html to 'read_html' is deprecated and                  
                             will be removed in a future version. To read from a literal string,                   
                             wrap it in a 'StringIO' object.                                                       
                               df_home = pd.read_html(home_html)[0]                                                
                                                                                                                   

                    WARNING  C:\Users\ASUS\AppData\Local\Temp\ipykernel_27668\1651500141.py:60:     ]8;id=126635;file://C:\Users\ASUS\anaconda3\envs\fb\lib\warnings.py\warnings.py]8;;\:]8;id=760813;file://C:\Users\ASUS\anaconda3\envs\fb\lib\warnings.py#109\109]8;;\
                             FutureWarning: Passing literal html to 'read_html' is deprecated and                  
                             will be removed in a future version. To read from a literal string,                   
                             wrap it in a 'StringIO' object.                                                       
                               df_away = pd.read_html(away_html)[0]                                                
                                                                                                                   

InvalidSessionIdException: Message: invalid session id: session deleted as the browser has closed the connection
from disconnected: unable to send message to renderer
  (Session info: chrome=143.0.7499.42); For documentation on this error, please visit: https://www.selenium.dev/documentation/webdriver/troubleshooting/errors#invalidsessionidexception
Stacktrace:
Symbols not available. Dumping unresolved backtrace:
	0x7ff631b98245
	0x7ff631b982a0
	0x7ff63197165d
	0x7ff63195d82c
	0x7ff63195d78c
	0x7ff63195bfaa
	0x7ff63195cbcf
	0x7ff63196c094
	0x7ff63198223f
	0x7ff63198940a
	0x7ff63195d375
	0x7ff6319818e4
	0x7ff631a1b080
	0x7ff6319bac29
	0x7ff6319bba93
	0x7ff631eaffe0
	0x7ff631eaa920
	0x7ff631ec9086
	0x7ff631bb5744
	0x7ff631bbe6ec
	0x7ff631ba1964
	0x7ff631ba1b15
	0x7ff631b87842
	0x7ffb659de8d7
	0x7ffb663ac53c
